In [1]:
# Imports
import numpy as np
import pandas as pd
import tensorflow as tf

from tensorflow.keras import activations, losses, metrics, optimizers, callbacks, Sequential
from tensorflow.keras.layers import Dense, MaxPooling2D, Conv2D, Dropout, Flatten, InputLayer
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split
from tensorflow.keras.activations import relu, softmax
from tensorflow.keras import datasets
from keras_tuner import RandomSearch, HyperParameters, SklearnTuner


In [2]:
num_classes = 10
input_shape = (28, 28, 1)

In [3]:
# Read data
data = pd.read_csv('../data/train.csv', header=0)

X_train, X_test, y_train, y_test = train_test_split(
    data.drop('label', axis=1),
    data['label'],
    test_size=.2,
    random_state=42
)

In [4]:
# Keras data
(X_train_keras, y_train_keras), (X_test_keras, y_test_keras) = datasets.mnist.load_data()
X_train_keras = np.expand_dims(X_train_keras, -1).astype('float32')
X_test_keras = np.expand_dims(X_test_keras, -1).astype('float32')

# Prepare
y_train = to_categorical(y_train.to_numpy(), num_classes)
y_test = to_categorical(y_test.to_numpy(), num_classes)
y_train_keras = to_categorical(y_train_keras, num_classes)
y_test_keras = to_categorical(y_test_keras, num_classes)

# Reshape
X_train = X_train.to_numpy().reshape(-1, *input_shape)
X_test = X_test.to_numpy().reshape(-1, *input_shape)

# Concat
X_train = np.vstack((X_train, X_train_keras, X_test_keras))
y_train = np.vstack((y_train, y_train_keras, y_test_keras))


# Normalising
X_train = X_train / 255.
X_test = X_test / 255.

In [13]:
model = Sequential([
    Conv2D(
        filters=16,
        kernel_size=(4, 4),
        activation=relu,
        input_shape=input_shape,
        padding='same'
    ),
    MaxPooling2D(
        pool_size=(3, 3),
        strides=2,
        padding='same'
    ),
    Conv2D(
        filters=64,
        kernel_size=(3, 3),
        activation=relu,
        padding='same'
    ),
    MaxPooling2D(pool_size=(2, 2)),
    Conv2D(
        filters=128,
        kernel_size=(3, 3),
        activation=relu,
        padding='same'
    ),
    MaxPooling2D(pool_size=(2, 2)),
    Conv2D(
        filters=256,
        kernel_size=(3, 3),
        activation=relu,
        padding='same'
    ),
    MaxPooling2D(pool_size=(2, 2)),
    Flatten(),
    Dense(units=256, activation=relu),
    Dropout(rate=.5),
    Dense(units=128, activation=relu),
    Dropout(rate=.5),
    Dense(units=num_classes, activation=softmax)
])

model.summary()

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_12 (Conv2D)           (None, 28, 28, 16)        272       
_________________________________________________________________
max_pooling2d_12 (MaxPooling (None, 14, 14, 16)        0         
_________________________________________________________________
conv2d_13 (Conv2D)           (None, 14, 14, 64)        9280      
_________________________________________________________________
max_pooling2d_13 (MaxPooling (None, 7, 7, 64)          0         
_________________________________________________________________
conv2d_14 (Conv2D)           (None, 7, 7, 128)         73856     
_________________________________________________________________
max_pooling2d_14 (MaxPooling (None, 3, 3, 128)         0         
_________________________________________________________________
conv2d_15 (Conv2D)           (None, 3, 3, 256)        

In [14]:
callback = callbacks.EarlyStopping()

model.compile(
    loss=losses.categorical_crossentropy,
    optimizer=optimizers.Adam(),
    metrics=[metrics.Accuracy(), metrics.MeanSquaredError()]
)

In [15]:
history = model.fit(
    X_train, y_train,
    batch_size=32,
    epochs=12,
    verbose=1
)

Epoch 1/12
3238/3238 [==============================] - 148s 45ms/step - loss: 0.1843 - accuracy: 0.0098 - mean_squared_error: 0.0076

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.


KeyboardInterrupt



In [10]:
test = pd.read_csv('../data/test.csv', header=0)

In [11]:
pd.DataFrame({
    'ImageId': test.index + 1,
    'Label': np.argmax(
        model.predict(
            test.to_numpy()
                .reshape(-1, 28, 28, 1)
        ), axis=-1)
}).to_csv('../submissions/best.csv', index=False)

#### Hyper parameters tuning

In [18]:
!pip install keras-tuner -q

In [58]:
def build_simple_model(hp: HyperParameters):
    model = Sequential()
    model.add(InputLayer(input_shape=input_shape))
    model.add(Flatten())
    for i in range(hp.Int('num_layers', min_value=2, max_value=20)):
        model.add(Dense(
            units=hp.Int('units_'+ str(i), min_value=32, max_value=128, step=32),
            activation=relu
        ))
        model.add(Dropout(.5))

    model.add(Dense(10, activation=softmax))

    model.compile(
        optimizer=optimizers.Adam(
            hp.Choice('learning_rate', [1e-2, 1e-3, 1e-4])
        ),
        loss=losses.categorical_crossentropy,
        metrics=[metrics.categorical_accuracy]
    )

    return model

In [44]:
def build_convolutional_model(hp: HyperParameters):
    model = Sequential()
    model.add(
        Conv2D(
            filters=16,
            kernel_size=(4, 4),
            activation=relu,
            input_shape=input_shape,
            padding='same'
        )
    )
    model.add(MaxPooling2D(pool_size=(3, 3), strides=2, padding='same'))

    for i in range(hp.Int('num_layers', min_value=1, max_value=3)):
        model.add(
            Conv2D(
                filters=hp.Choice('filters_'+ str(i), [32, 64, 128]),
                kernel_size=(3, 3),
                padding='same',
                activation=relu
            )
        )
        model.add(MaxPooling2D(pool_size=(2, 2), strides=2))

    model.add(Flatten())
    model.add(Dense(64, activation=relu))
    model.add(Dense(10, activation=softmax))

    model.compile(
        optimizer=optimizers.Adam(
            hp.Choice('learning_rate', [1e-3, 1e-4])
        ),
        loss=losses.categorical_crossentropy,
        metrics=[metrics.categorical_accuracy]
    )

    return model

In [94]:
tuner = RandomSearch(
    build_simple_model,
    objective='val_categorical_accuracy',
    max_trials=3,
    executions_per_trial=2,
    overwrite=True,
    directory='models',
    project_name='mnist_keras'
)

In [95]:
tuner.search(
    X_train, y_train,
    verbose=1, epochs=3,
    validation_data=(X_test, y_test)
)


Search: Running Trial #1

Hyperparameter    |Value             |Best Value So Far 
num_layers        |13                |?                 
units_0           |96                |?                 
units_1           |96                |?                 
learning_rate     |0.001             |?                 

Epoch 1/3
 494/1050 [=============>................] - ETA: 1s - loss: 2.2620 - categorical_accuracy: 0.1688   

KeyboardInterrupt: 

In [57]:
model = tuner.get_best_models(1)[0]

pd.DataFrame({
    'ImageId': test.index + 1,
    'Label': np.argmax(
        model.predict(
            test.to_numpy()
                .reshape(-1, 28, 28, 1)
        ), axis=-1)
}).to_csv('../submissions/randomsearch.csv', index=False)

In [1]:
from tensorflow.keras import datasets


In [45]:
convolutional_tuner = RandomSearch(
    build_convolutional_model,
    objective='val_categorical_accuracy',
    max_trials=3,
    executions_per_trial=2,
    overwrite=True,
    directory='models',
    project_name='mnist_keras'
)

In [47]:
convolutional_tuner.search(
    X_train, y_train,
    verbose=1, epochs=3,
    validation_data=(X_test, y_test)
)

Trial 2 Complete [00h 08m 33s]
val_categorical_accuracy: 0.982142835855484

Best val_categorical_accuracy So Far: 0.982142835855484
Total elapsed time: 00h 15m 59s

Search: Running Trial #3

Hyperparameter    |Value             |Best Value So Far 
num_layers        |1                 |1                 
filters_0         |256               |32                
learning_rate     |0.01              |0.0001            

Epoch 1/3
 661/3238 [=====>........................] - ETA: 4:11 - loss: 0.3013 - categorical_accuracy: 0.9083 

KeyboardInterrupt: 

In [101]:
model = convolutional_tuner.get_best_models(1)[0]

pd.DataFrame({
    'ImageId': test.index + 1,
    'Label': np.argmax(
        model.predict(
            test.to_numpy()
                .reshape(-1, 28, 28, 1)
        ), axis=-1)
}).to_csv('../submissions/randomsearch_conv.csv', index=False)

In [103]:

convolutional_tuner.search(
    X_train, y_train,
    verbose=1, epochs=10,
    validation_data=(X_test, y_test)
)

INFO:tensorflow:Oracle triggered exit


In [104]:
model = convolutional_tuner.get_best_models(1)[0]

pd.DataFrame({
    'ImageId': test.index + 1,
    'Label': np.argmax(
        model.predict(
            test.to_numpy()
                .reshape(-1, 28, 28, 1)
        ), axis=-1)
}).to_csv('../submissions/randomsearch_conv2.csv', index=False)